In [1]:
from typing import List, Optional, Any
import torch
import torch.utils.data
import numpy as np
import random
from math import inf 

import datetime

import transformers
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig
from transformers import MT5Tokenizer, MT5ForConditionalGeneration, AutoModelForSeq2SeqLM, DataCollatorForSeq2Seq, Seq2SeqTrainingArguments, Seq2SeqTrainer

from peft import LoraConfig
from trl import SFTTrainer
import datasets
import time

import json
import os
import cqlcmp
import cql_checker
import lark

In [2]:
torch.manual_seed(21)
torch.cuda.manual_seed_all(21)
np.random.seed(21)
random.seed(21)
#torch.backends.cudnn.deterministic = True
#torch.backends.cudnn.benchmark = False

In [3]:
device = torch.device("cuda")

In [4]:
class DatasetNatural2CQL(torch.utils.data.Dataset):
    def __init__(self, path: Optional[str] = None) -> None:
        self.sentence_freq = []
        self.cql2nl = []
        self.nl2cql = []
        self.natural_language_rulebased = []
        self.cql = []
        self.natural_language = []
        self.enabled_natural_language = []

        if path is not None:
            self.load_tsv(path)

    def enable_cql(self, cqls):
        self.enabled_natural_language = []
        for cql in cqls:
            for p in cql:
                self.enabled_natural_language.append(p)

    def dump_json(self, filepath: str) -> None:
        with open(filepath, "w") as file:
            for i in range(len(self)):
                data = json.dumps(self[i])
                file.write(data)
                file.write("\n")

    def add_translation(self, freq: int, cql: str, natural_language_rulebased: str, natural_language: List[str]) -> None:
        cql_index = len(self.sentence_freq)
        self.sentence_freq.append(freq)
        self.cql.append(cql)
        self.natural_language_rulebased.append(natural_language_rulebased)
        self.cql2nl.append([])

        for sentence in natural_language:
            self.nl2cql.append(cql_index)
            self.cql2nl[-1].append(len(self.natural_language))
            self.natural_language.append(sentence)

    def load_tsv(self, path: str) -> None:
        with open(path, "r") as file_data:
            for line in file_data:
                line = line.strip()
                line = line.split("\t")
                texts_json = json.loads(line[4])
                texts_extracted = texts_json["data"][0]["content"][0]["text"]["value"].split("\n")
                self.add_translation(int(line[0]), line[2], line[3], texts_extracted)

    def __len__(self):
        return len(self.enabled_natural_language)

    def __getitem__(self, idx):
        if idx < len(self.nl2cql):
            return {"text": self.natural_language[self.enabled_natural_language[idx]], "cql": self.cql[self.nl2cql[self.enabled_natural_language[idx]]]}
        return None

In [5]:
dataset = DatasetNatural2CQL("expand_natural_texts_0004.res.tsv")

In [6]:
validation_cqls = []
with open("test_ids.json", "r") as file:
    validation_cqls = json.load(file)

In [7]:
dataset.enable_cql(validation_cqls)

In [8]:
len(dataset)

4280

In [9]:
model_name = "google/mt5-base"
tokenizer = MT5Tokenizer.from_pretrained(model_name)
model = MT5ForConditionalGeneration.from_pretrained(model_name, device_map={"":0})

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'T5Tokenizer'. 
The class this function is called from is 'MT5Tokenizer'.
You are using the default legacy behaviour of the <class 'transformers.models.mt5.tokenization_mt5.MT5Tokenizer'>. This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thoroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565


In [10]:
import os

path = 'models/google-mt5_t5-base'

# List all folders (directories) in the given path
folders = [name for name in os.listdir(path) if not os.path.isdir(os.path.join(path, name))]

In [11]:
def f_in(data):
    full_input = "translate: " + data
    return full_input

In [12]:
#random.shuffle(dataset.enabled_natural_language)

i = 0
while i < len(dataset):
    dataset.natural_language[dataset.enabled_natural_language[i]] = f_in(dataset.natural_language[dataset.enabled_natural_language[i]])
    i += 1

In [13]:
def get_text(text):
    text = text.split("translate: ", 1)[1]
    return text

In [14]:
class CQLLogitsProcessor(transformers.generation.logits_process.LogitsProcessor):
    def __init__(self, id2string, verbose = False):
        self.id2string = id2string
        self.checker = cql_checker.CQLChecker()
        self.checker.eos_token_id = 1
        self.verbose = verbose
        self.text = ""

    def __call__(self, input_ids: torch.LongTensor, scores: torch.FloatTensor):
        scores[0][2] = -inf
        scores[0][3] = -inf
        if len(self.text) == 0:
            scores[0][784] = inf
            self.text = "["
            return scores
        while True:
            token_id = int(np.argmax(scores[0].to("cpu")))
            if token_id < 32000:
                text_copy = self.text
                text_copy += self.id2string[token_id]
                is_error = False
                try:
                    self.checker.parse(text_copy)
                except lark.exceptions.UnexpectedEOF:
                    if token_id == self.checker.eos_token_id:
                        is_error = True
                except Exception:
                    is_error = True
                if not is_error:
                    scores[0][token_id] = inf
                    self.text = text_copy
                    if self.verbose:
                        print("Accepted: ", self.id2string[token_id])
                    break
            scores[0][token_id] = -inf
            if self.verbose:
                print("Rejected: ", self.id2string[token_id])
        return scores

In [15]:
id2token = tokenizer.convert_ids_to_tokens(list(range(tokenizer.vocab_size)))
id2string = []
for token in id2token:
    id2string.append(tokenizer.convert_tokens_to_string([token]))
processor = CQLLogitsProcessor(id2string, False)
logits_processor_list = transformers.generation.logits_process.LogitsProcessorList([
    processor,
])

In [ ]:
with open("test_results_logits.tsv", "w") as test_tsv:
    with open("test_log.txt_logits", "w") as log:
        for folder in folders:
            start_time = int(time.time())
            adapter_model_name = 'models/google-mt5_t5-base/' + folder

            if folder != "model_train_data_1_1000.pt":
                continue
            
            model.load_state_dict(torch.load(adapter_model_name, weights_only=True))
            model.eval()
            dataloader = torch.utils.data.DataLoader(dataset, batch_size=1, shuffle=False)
            blue_sum = 0
            blue_size = 0
            batch_id = 0
            for batch in dataloader:
                batch_id += 1
                inputs = tokenizer(batch["text"], truncation=True, max_length=1024, return_tensors="pt", padding=True).to(device)
                outputs = model.generate(**inputs, max_new_tokens=100, logits_processor=logits_processor_list)
                processor.text = ""
                for i, output in enumerate(outputs):
                    cql = tokenizer.decode(output, skip_special_tokens=True).replace("<extra_id_0>", "")
                    cql_ids = cqlcmp.cql_tokenizer(cql)
                    gold_cql_ids = cqlcmp.cql_tokenizer(batch["cql"][i])
                    bleu = cqlcmp.sentence_bleu([gold_cql_ids], cql_ids, weights=(0.25, 0.25, 0.25, 0.25))
                    blue_sum += bleu
                    blue_size += 1
                    test_result = [cql.replace("\n", " "), batch["cql"][i], get_text(batch["text"][i])]
                    print("\t".join(test_result))
                    print("\t".join(test_result), file=test_tsv)
                to_log = ""
                to_log += "Working on: " + adapter_model_name + " | "
                to_log += str(blue_size) + "/" + str(len(dataset)) + " | "
                to_log += "AVG Bleu: " + str(blue_sum/blue_size) + " | "
                to_log += "Time: " + str(int(time.time())-start_time) + " | "
                try:
                    to_log += "ETA: " + str(int((int(time.time())-start_time)/(blue_size/len(dataset)*(1-(blue_size/len(dataset)))))) + " sec" + " | "
                except:
                    to_log += "ETA: " + "0" + " sec" + " | "
                
                print(to_log, file=log)
                log.flush()
                test_tsv.flush()
                print(to_log)
            

mai!tag="DT|J.*|N.*|N.*"] [word="man"]	[tag !="DT" & tag !="JJ.*" & tag !="CD" & tag !="N.*"] [word="man"]	All tokens that are not determiners, adjectives, cardinal numbers, or nouns followed by the word "man."
Working on: models/google-mt5_t5-base/model_train_data_1_1000.pt | 1/4280 | AVG Bleu: 0.3089600783952219 | Time: 4 | ETA: 17124 sec | 
mai!tag="N.*"] [word="man"]	[tag !="DT" & tag !="JJ.*" & tag !="CD" & tag !="N.*"] [word="man"]	Any token that does not match the tags DT, JJ, CD, or is not a noun, followed by the word "man."
Working on: models/google-mt5_t5-base/model_train_data_1_1000.pt | 2/4280 | AVG Bleu: 0.26209121678651026 | Time: 4 | ETA: 8564 sec | 
maitag="DT" & tag="J.*"] [tag="N.*"] [word="man"]	[tag !="DT" & tag !="JJ.*" & tag !="CD" & tag !="N.*"] [word="man"]	Non-determiner, non-adjective, non-number, and non-noun tokens that precede the word "man."
Working on: models/google-mt5_t5-base/model_train_data_1_1000.pt | 3/4280 | AVG Bleu: 0.3373551728119803 | Time: 5 |

/mnt/asteria02/thor1/asteria04_mnt_local2/xmikusek/aiproject/.venv/lib/python3.10/site-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/mnt/asteria02/thor1/asteria04_mnt_local2/xmikusek/aiproject/.venv/lib/python3.10/site-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/mnt/asteria02/thor1/asteria04_mnt_local2/xmikusek/aiproject/.venv/lib/python3.10/site-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU sc

mai ]	[lemma="staff"&tag="V.P|V.Z"]	All verbs related to the lemma staff tagged with V.P or V.Z.  
Working on: models/google-mt5_t5-base/model_train_data_1_1000.pt | 8/4280 | AVG Bleu: 0.24060313121637658 | Time: 9 | ETA: 4824 sec | 
mai ]	[lemma="staff"&tag="V.P|V.Z"]	Lemma staff appearing as a verb in past or present tense.  
Working on: models/google-mt5_t5-base/model_train_data_1_1000.pt | 9/4280 | AVG Bleu: 0.2138694499701125 | Time: 9 | ETA: 4289 sec | 
mai ]	[lemma="staff"&tag="V.P|V.Z"]	Any verb with the lemma staff that matches the tags V.P or V.Z.  
Working on: models/google-mt5_t5-base/model_train_data_1_1000.pt | 10/4280 | AVG Bleu: 0.19248250497310126 | Time: 9 | ETA: 3861 sec | 
mai ] [tag="V.P|V.Z"]	[lemma="staff"&tag="V.P|V.Z"]	Staff as a lemma combined with verb tags V.P or V.Z.  
Working on: models/google-mt5_t5-base/model_train_data_1_1000.pt | 11/4280 | AVG Bleu: 0.23010979532390935 | Time: 10 | ETA: 3900 sec | 
mai ]	[lemma="staff"&tag="V.P|V.Z"]	Tokens with staff 